In [73]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt


from preprocessor import clean

from transformers import TFAutoModelForSeq2SeqLM, AutoTokenizer, pipeline
import nltk
from nltk.sentiment import SentimentIntensityAnalyzer

In [42]:
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     /home/coder/nltk_data...


True

In [43]:
sent_model = SentimentIntensityAnalyzer()

In [23]:
datapath = os.path.join("..","data","elonmusk.csv")
full_data = pd.read_csv(datapath)

In [24]:
full_data["Datetime"] = full_data["Datetime"].astype(str).str[:8] ### for months only

for idx, row in full_data.iterrows():
    text = row["Text"]
    text = str(text)
    text = clean(text)
    full_data["Text"].iloc[idx] = text

full_data["Text"].replace("", np.nan, inplace=True)
full_data.dropna(subset="Text", inplace=True)

/tmp/ipykernel_199/2427706158.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  full_data["Text"].iloc[idx] = text
/tmp/ipykernel_199/2427706158.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  full_data["Text"].iloc[idx] = text
/tmp/ipykernel_199/2427706158.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  full_data["Text"].iloc[idx] = text
/tmp/ipykernel_199/2427706158.py:7: SettingWithCopyWarning: 
A value is trying to be set

In [29]:
full_data

Datetime             Tweet Id  \
0      2023-05-28  1662950185230651392   
1      2023-05-28  1662910256161124352   
2      2023-05-28  1662907251701448705   
3      2023-05-28  1662906483376308228   
4      2023-05-28  1662764138043518977   
...           ...                  ...   
23457  2011-12-03   142881284019060736   
23458  2011-12-03   142880871391838208   
23459  2011-12-01   142188458125963264   
23460  2011-12-01   142179928203460608   
23461  2010-06-04          15434727182   

                                                    Text  Username  
0               Whole podcast uploaded to this platform!  elonmusk  
1      Youre such a numbskull. Please point out where...  elonmusk  
2                                                      ?  elonmusk  
3                                         Major problem!  elonmusk  
4                     For obvious &amp; sensible reasons  elonmusk  
...                                                  ...       ...  
23457                  That was a total non sequitur btw  elonmusk  
23458  Great Voltaire quote, arguably better than Twa...  elonmusk  
23459  I made the volume on the Model S go to . Now I...  elonmusk  
23460  Went to Iceland on Sat to ride bumper cars on ...  elonmusk  
23461  Please ignore prior tweets, as that was someon...  elonmusk  

[21337 rows x 4 columns]

In [50]:
tweet_list = list(full_data["Text"])

In [65]:
sentiments = []

for element in tweet_list:
    sentiment = sent_model.polarity_scores(element)
    #print(sentiment)
    max_sent = max(sentiment, key=sentiment.get)
    #print(max_sent)
    sentiments.append(max_sent)



In [83]:
date_sent = pd.DataFrame({"Timestamp": full_data["Datetime"], "Text": full_data["Text"], "Sentiment": sentiments})

In [84]:
date_sent

Timestamp                                               Text Sentiment
0       2023-05           Whole podcast uploaded to this platform!       neu
1       2023-05  Youre such a numbskull. Please point out where...       neu
2       2023-05                                                  ?       neg
3       2023-05                                     Major problem!       neg
4       2023-05                 For obvious &amp; sensible reasons       neu
...         ...                                                ...       ...
23457   2011-12                  That was a total non sequitur btw       neu
23458   2011-12  Great Voltaire quote, arguably better than Twa...  compound
23459   2011-12  I made the volume on the Model S go to . Now I...       neu
23460   2011-12  Went to Iceland on Sat to ride bumper cars on ...  compound
23461   2010-06  Please ignore prior tweets, as that was someon...       neu

[21337 rows x 3 columns]

In [112]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-large")
trained_tokenizer = tokenizer.train_new_from_iterator(tweet_list, 32000)

In [113]:
model = TFAutoModelForSeq2SeqLM.from_pretrained("google/flan-t5-large")

/home/coder/.local/lib/python3.9/site-packages/keras/initializers/initializers.py:120: UserWarning: The initializer RandomNormal is unseeded and being called multiple times, which will return identical values each time (even if the initializer is unseeded). Please update your code to provide a seed to the initializer, or avoid using the same initalizer instance more than once.
  warnings.warn(
All model checkpoint layers were used when initializing TFT5ForConditionalGeneration.

All the layers of TFT5ForConditionalGeneration were initialized from the model checkpoint at google/flan-t5-large.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFT5ForConditionalGeneration for predictions without further training.


In [123]:
import tensorflow as tf
from transformers import TFGPT2LMHeadModel, GPT2Tokenizer

In [124]:
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")


All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at gpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


In [132]:
tokenizer.add_special_tokens({'pad_token': '[PAD]'})  # Add a new padding token

input_ids = []
attention_masks = []

for text in tweet_list:
    encoded = tokenizer.encode_plus(
        text,
        add_special_tokens=True,
        max_length=280,
        padding="max_length",
        truncation=True,
        return_attention_mask=True,
        return_tensors="tf"
    )
    
    input_ids.append(encoded["input_ids"])
    attention_masks.append(encoded["attention_mask"])

input_ids = tf.concat(input_ids, axis=0)
attention_masks = tf.concat(attention_masks, axis=0)

tf.data.Dataset.from_tensor_slices((input_ids, attention_masks))

<_TensorSliceDataset element_spec=(TensorSpec(shape=(280,), dtype=tf.int32, name=None), TensorSpec(shape=(280,), dtype=tf.int32, name=None))>

In [133]:
# add the EOS token as PAD token to avoid warnings
model = TFGPT2LMHeadModel.from_pretrained("gpt2", pad_token_id=tokenizer.eos_token_id)

All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at gpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


In [136]:
# encode context the generation is conditioned on
input_ids = tokenizer.encode('Trump has been', return_tensors='tf')

In [137]:
# set seed to reproduce results. Feel free to change the seed though to get different results
tf.random.set_seed(0)

# set top_k = 50 and set top_p = 0.95 and num_return_sequences = 3
sample_outputs = model.generate(
    input_ids,
    do_sample=True, 
    max_length=50, 
    top_k=50, 
    top_p=0.95 ##, 
    ## num_return_sequences=3
)

print("Output:\n" + 100 * '-')
for i, sample_output in enumerate(sample_outputs):
  print("{}: {}".format(i, tokenizer.decode(sample_output, skip_special_tokens=True)))

Output:
----------------------------------------------------------------------------------------------------
0: Trump has been working on the White House project since September 2013, during which time he has made extensive use of government contracts, such as $9.3 million, of which $2.3 million came from the Office of the Director of National Intelligence


In [120]:
inputs = trained_tokenizer(prompt, 
                    max_length = 280,
                    return_tensors="tf",
                    truncation=True)

outputs = model.generate(**inputs)

In [121]:
print(tokenizer.batch_decode(outputs, 
                             skip_special_tokens=True))

['sa sa sa sa sa sa ']


In [100]:
model = TFAutoModelForSeq2SeqLM.from_pretrained("google/flan-t5-base")

/home/coder/.local/lib/python3.9/site-packages/keras/initializers/initializers.py:120: UserWarning: The initializer RandomNormal is unseeded and being called multiple times, which will return identical values each time (even if the initializer is unseeded). Please update your code to provide a seed to the initializer, or avoid using the same initalizer instance more than once.
  warnings.warn(
All model checkpoint layers were used when initializing TFT5ForConditionalGeneration.

All the layers of TFT5ForConditionalGeneration were initialized from the model checkpoint at google/flan-t5-base.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFT5ForConditionalGeneration for predictions without further training.


In [3]:
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-base")

In [10]:
# classification
#prompt = "classify the following text as positive or negative: I absolutely hated this movie"

# translation
#prompt = "translate from English to French: how old are you?"

# question answering
prompt = "answer the following question: how is cheese made?"

# named entity recognition
#prompt = "find all location entities in this text: Ross comes from Scotland"

In [11]:
inputs = tokenizer(prompt, 
                    max_length = 280,
                    return_tensors="tf",
                    truncation=True)

In [14]:
outputs = model.generate(**inputs)

In [15]:
print(tokenizer.batch_decode(outputs, 
                             skip_special_tokens=True))

['a process']
